# MLflow
</br><img style="width: 50%;" src="img/expcontrol/mlflow-logo-d.png"/>


 ## MLflow
  - https://mlflow.org/
  - Narzędzie podobne do omawianego na poprzednich zajęciach Sacred
  - Nieco inne podejście: mniej ingerencji w istniejący kod
  - Bardziej kompleksowe rozwiązanie: 4 komponenty, pierwszy z nich ma funkcjonalność podobną do Sacred
  - Działa "z każdym" językiem. A tak naprawdę: Python, R, Java + CLI API + REST API
  - Popularna wśród pracodawców - wyniki wyszukiwania ofert pracy: 20 ofert (https://pl.indeed.com/), 36 ofert (linkedin). Sacred: 0
  - Integracja z licznymi bibliotekami / chmurami


## Komponenty

MLflow składa się z czterech niezależnych komponentów:
 - **MLflow Tracking** - pozwala śledzić zmiany parametrów, kodu, środowiska i ich wpływ na metryki. Jest to funkcjonalność bardzo zbliżona do tej, którą zapewnia Sacred
 - **MLflow Projects** - umożliwia "pakowanie" kodu ekserymentów w taki sposób, żeby mogłby być w łatwy sposób zreprodukowane przez innych
 - **MLflow Models** - ułatwia "pakowanie" modeli uczenia maszynowego
 - **MLflow Registry** - zapewnia centralne miejsce do przechowywania i współdzielenia modeli. Zapewnia narzędzia do wersjonowania i śledzenia pochodzenia tych modeli.
 
Komponenty te mogą być używane razem bądź oddzielnie.

## MLflow Tracking - przykład
(poniższe przykłady kodu trenującego pochodzą z tutoriala MLflow: https://mlflow.org/docs/latest/tutorials-and-examples/tutorial.html)

In [45]:
%%capture null
!pip install mlflow
!pip install sklearn

In [19]:
%%writefile IUM_08/examples/sklearn_elasticnet_wine/train.py
# The data set used in this example is from http://archive.ics.uci.edu/ml/datasets/Wine+Quality
# P. Cortez, A. Cerdeira, F. Almeida, T. Matos and J. Reis.
# Modeling wine preferences by data mining from physicochemical properties. In Decision Support Systems, Elsevier, 47(4):547-553, 2009.

import os
import warnings
import sys

import pandas as pd
import numpy as np
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from sklearn.model_selection import train_test_split
from sklearn.linear_model import ElasticNet
from urllib.parse import urlparse
import mlflow
import mlflow.sklearn

import logging

logging.basicConfig(level=logging.WARN)
logger = logging.getLogger(__name__)


def eval_metrics(actual, pred):
    rmse = np.sqrt(mean_squared_error(actual, pred))
    mae = mean_absolute_error(actual, pred)
    r2 = r2_score(actual, pred)
    return rmse, mae, r2


if __name__ == "__main__":
    warnings.filterwarnings("ignore")
    np.random.seed(40)

    # Read the wine-quality csv file from the URL
    csv_url = (
        "http://archive.ics.uci.edu/ml/machine-learning-databases/wine-quality/winequality-red.csv"
    )
    try:
        data = pd.read_csv(csv_url, sep=";")
    except Exception as e:
        logger.exception(
            "Unable to download training & test CSV, check your internet connection. Error: %s", e
        )

    # Split the data into training and test sets. (0.75, 0.25) split.
    train, test = train_test_split(data)

    # The predicted column is "quality" which is a scalar from [3, 9]
    train_x = train.drop(["quality"], axis=1)
    test_x = test.drop(["quality"], axis=1)
    train_y = train[["quality"]]
    test_y = test[["quality"]]

    
    alpha = float(sys.argv[1]) if len(sys.argv) > 1 else 0.5
    #alpha = 0.5
    l1_ratio = float(sys.argv[2]) if len(sys.argv) > 2 else 0.5
    #l1_ratio = 0.5

    with mlflow.start_run():
        lr = ElasticNet(alpha=alpha, l1_ratio=l1_ratio, random_state=42)
        lr.fit(train_x, train_y)

        predicted_qualities = lr.predict(test_x)

        (rmse, mae, r2) = eval_metrics(test_y, predicted_qualities)

        print("Elasticnet model (alpha=%f, l1_ratio=%f):" % (alpha, l1_ratio))
        print("  RMSE: %s" % rmse)
        print("  MAE: %s" % mae)
        print("  R2: %s" % r2)

        mlflow.log_param("alpha", alpha)
        mlflow.log_param("l1_ratio", l1_ratio)
        mlflow.log_metric("rmse", rmse)
        mlflow.log_metric("r2", r2)
        mlflow.log_metric("mae", mae)

        tracking_url_type_store = urlparse(mlflow.get_tracking_uri()).scheme

        # Model registry does not work with file store
        if tracking_url_type_store != "file":

            # Register the model
            # There are other ways to use the Model Registry, which depends on the use case,
            # please refer to the doc for more information:
            # https://mlflow.org/docs/latest/model-registry.html#api-workflow
            mlflow.sklearn.log_model(lr, "model", registered_model_name="ElasticnetWineModel")
        else:
            mlflow.sklearn.log_model(lr, "model")

Overwriting IUM_08/examples/sklearn_elasticnet_wine/train.py


In [32]:
### Wtyrenujmy model z domyślnymi wartościami parametrów
! cd ./IUM_08/examples/; python sklearn_elasticnet_wine/train.py

Elasticnet model (alpha=0.500000, l1_ratio=0.500000):
  RMSE: 0.7931640229276851
  MAE: 0.6271946374319586
  R2: 0.10862644997792614


In [37]:
### I jeszcze raz, tym razem ze zmienionymi wartościami parametrów
! cd ./IUM_08/examples/; for l in {1..9}; do for a in {1..9}; do python sklearn_elasticnet_wine/train.py 0.$a 0.$l; done; done

Elasticnet model (alpha=0.100000, l1_ratio=0.100000):
  RMSE: 0.7128829045893679
  MAE: 0.5462202174984664
  R2: 0.2799376066653344
Elasticnet model (alpha=0.200000, l1_ratio=0.100000):
  RMSE: 0.7268133518615142
  MAE: 0.5586842416161892
  R2: 0.251521166881557
Elasticnet model (alpha=0.300000, l1_ratio=0.100000):
  RMSE: 0.7347397539240514
  MAE: 0.5657315547549873
  R2: 0.23510678899596094
Elasticnet model (alpha=0.400000, l1_ratio=0.100000):
  RMSE: 0.7410782793160982
  MAE: 0.5712718681984227
  R2: 0.22185255063708875
Elasticnet model (alpha=0.500000, l1_ratio=0.100000):
  RMSE: 0.7460550348172179
  MAE: 0.576381895873763
  R2: 0.21136606570632266
Elasticnet model (alpha=0.600000, l1_ratio=0.100000):
  RMSE: 0.7510866447955419
  MAE: 0.5815681289333974
  R2: 0.20069264568704714
Elasticnet model (alpha=0.700000, l1_ratio=0.100000):
  RMSE: 0.7560654760040749
  MAE: 0.5868129921328281
  R2: 0.19006056603695476
Elasticnet model (alpha=0.800000, l1_ratio=0.100000):
  RMSE: 0.760926370

Elasticnet model (alpha=0.900000, l1_ratio=0.700000):
  RMSE: 0.8331069437643933
  MAE: 0.6697424890266508
  R2: 0.016588601539516357
Elasticnet model (alpha=0.100000, l1_ratio=0.800000):
  RMSE: 0.7339712501091269
  MAE: 0.5654097809725043
  R2: 0.23670603806205326
Elasticnet model (alpha=0.200000, l1_ratio=0.800000):
  RMSE: 0.7552646505492441
  MAE: 0.5873472009739388
  R2: 0.19177543499093674
Elasticnet model (alpha=0.300000, l1_ratio=0.800000):
  RMSE: 0.7836957692333741
  MAE: 0.6176788505535867
  R2: 0.12978065429593022
Elasticnet model (alpha=0.400000, l1_ratio=0.800000):
  RMSE: 0.8160164529135189
  MAE: 0.650349905850893
  R2: 0.05652247327326554
Elasticnet model (alpha=0.500000, l1_ratio=0.800000):
  RMSE: 0.8320145539945119
  MAE: 0.6657081587004348
  R2: 0.019165855890777572
Elasticnet model (alpha=0.600000, l1_ratio=0.800000):
  RMSE: 0.8326325509502465
  MAE: 0.6676500690618903
  R2: 0.01770824285088779
Elasticnet model (alpha=0.700000, l1_ratio=0.800000):
  RMSE: 0.8331

In [23]:
### Informacje o przebieagach eksperymentu zostały zapisane w katalogu mlruns
! ls -l IUM_08/examples/mlruns/0

total 16
drwxrwxr-x 6 tomek tomek 4096 maj  2 17:07 15918a3901854356933736dfc0935807
drwxrwxr-x 6 tomek tomek 4096 maj  2 16:36 23ae1069b29e4955ac9f3536c71e7ac2
drwxrwxr-x 6 tomek tomek 4096 maj  2 17:07 b7ddb17a37404d7898e105afa5c20287
-rw-rw-r-- 1 tomek tomek  151 maj  2 16:36 meta.yaml


In [1]:
### Możemy je obejrzeć w przeglądarce uruchamiając interfejs webowy:
### (powinniśmy to wywołać w normalnej konsoli, w jupyter będziemy mieli zablokowany kernel)
! cd IUM_08/examples/; mlflow ui

[2021-05-10 12:21:16 +0200] [20029] [INFO] Starting gunicorn 20.1.0
[2021-05-10 12:21:16 +0200] [20029] [INFO] Listening at: http://127.0.0.1:5000 (20029)
[2021-05-10 12:21:16 +0200] [20029] [INFO] Using worker: sync
[2021-05-10 12:21:16 +0200] [20030] [INFO] Booting worker with pid: 20030
^C
[2021-05-10 12:22:32 +0200] [20029] [INFO] Handling signal: int
[2021-05-10 12:22:32 +0200] [20030] [INFO] Worker exiting (pid: 20030)


### Wygląd interfejsu webowego
<img width="75%" src="IUM_08/mlflowui.png"/>

### Porównywanie wyników
<img width="75%" src="IUM_08/compare-metrics.png"/>

## Logowanie
 - logowania metryk i parametrów można dokonać m.in. poprzez wywołania Python-owego API: `mlflow.log_param()` i `mlflow.log_metric()`. Więcej dostępnych funkcji: [link](https://mlflow.org/docs/latest/tracking.html#logging-functions)
 - wywołania te muszą nastąpić po wykonaniu [`mlflow.start_run()`](https://mlflow.org/docs/latest/python_api/mlflow.html#mlflow.start_run), najlepiej wewnątrz bloku:
```python
   with mlflow.start_run():
        
        #[...]

        mlflow.log_param("alpha", alpha)
        mlflow.log_param("l1_ratio", l1_ratio)
```
 - jest też możliwość automatycznego logwania dla wybranych bibliotek: https://mlflow.org/docs/latest/tracking.html#automatic-logging

# MLflow Projects
 - MLflow projects to zestaw konwencji i kilku narzędzi
 - ułatwiają one uruchamianie eskperymentów

### Konfiguracja projektu
 - W pliku `MLproject` zapisuje się konfigurację projektu ([specyfikacja](https://mlflow.org/docs/latest/projects.html))
 - Zawiera ona:
    - odnośnik do środowiska, w którym ma być wywołany eksperyment [szczegóły](https://mlflow.org/docs/latest/projects.html#specifying-an-environment):
      - nazwa obrazu Docker
      - albo ścieżka do pliku conda.yaml definiującego środowisko wykonania Conda
    - parametry, z którymi można wywołać eksperyment
    - polecenia służące do wywołania eksperymentu

In [4]:
%%writefile IUM_08/examples/sklearn_elasticnet_wine/MLproject
name: tutorial

conda_env: conda.yaml #ścieżka do pliku conda.yaml z definicją środowiska
    
#docker_env:
#  image: mlflow-docker-example-environment

entry_points:
  main:
    parameters:
      alpha: {type: float, default: 0.5}
      l1_ratio: {type: float, default: 0.1}
    command: "python train.py {alpha} {l1_ratio}"
  test:
    parameters:
      alpha: {type: cutoff, default: 0}
    command: "python test.py {cutoff}"

Overwriting IUM_08/examples/sklearn_elasticnet_wine/MLproject


### Środowisko Conda
 </br><img style="height: 50px;" src="img/environments/conda.png"/>
 - https://docs.conda.io
 - Składnia plików conda.yaml definiujących środowisko: https://docs.conda.io/projects/conda/en/4.6.1/user-guide/tasks/manage-environments.html#create-env-file-manually
 - Składnia YAML: [przystępnie](https://learnxinyminutes.com/docs/yaml/), [oficjalnie](https://yaml.org/spec/1.2/spec.html)

In [1]:
%%writefile IUM_08/examples/sklearn_elasticnet_wine/conda.yaml
name: tutorial
channels:
  - defaults
dependencies:
  - python=3.6 #Te zależności będą zainstalowane za pomocą conda isntall
  - pip
  - pip: #Te ząś za pomocą pip install
    - scikit-learn==0.23.2
    - mlflow>=1.0

Overwriting IUM_08/examples/sklearn_elasticnet_wine/conda.yaml


### Środowisko docker
- zamiast środowiska Conda możemy również podać nazwę obrazu docker, w którym ma być wywołany eksperyment.
- obraz będzie szukany lokalnie a następnie na DockerHub, lub w innym repozytorium dockera
- składnia specyfikacji ścieżki jest taka sama jak w przypadki poleceń dockera, np. docker pull [link](https://docs.docker.com/engine/reference/commandline/pull/#pull-from-a-different-registry)
- Można również podać katalogi do podmontowania wewnątrz kontenera oraz wartości zmiennych środowiskowych do ustawienia w  kontenerze:
```yaml
docker_env:
   image: mlflow-docker-example-environment
   volumes: ["/local/path:/container/mount/path"]
   environment: [["NEW_ENV_VAR", "new_var_value"], "VAR_TO_COPY_FROM_HOST_ENVIRONMENT"]
```

### Parametry
 - Specyfikacja parametrów w pliku MLproject pozwala na ich walidację i używanie wartości domyślnych
 - Dostępne typy:
   - String
   - Float - dowolna liczba (MLflow waliduje, czy podana wartość jest liczbą)
   - Path - pozwala podawać ścieżki względne (przekształca je na bezwzlędne) do plików lokalnych albo do plików zdalnych (np. do s3://) - zostaną wtedy ściągnięte lokalnie
   - URI - podobnie jak path, ale do rozproszonych systemów plików

- [Składnia](https://mlflow.org/docs/latest/projects.html#specifying-parameters)
  
```yml:
  parameter_name: {type: data_type, default: value}  # Short syntax

  parameter_name:     # Long syntax
     type: data_type
     default: value
```

### Uruchamianie projektu
 - Projekt możemy uruchomić przy pomocy polecenia `mlflow run` ([dokumentacja](https://mlflow.org/docs/latest/cli.html#mlflow-run))
 - Spowoduje to przygotowanie środowiska i uruchomienie eksperymentu wewnątrz środowiska
 - domyślnie zostanie uruchomione polecenie zdefiniowane w "entry point" `main`. Żeby uruchomić inny "entry point", możemy użyć parametru `-e`, np:
 ```bash
 mlflow run sklearn_elasticnet_wine -e test
 ```

In [2]:
!cd IUM_08/examples/; mlflow run sklearn_elasticnet_wine -P alpha=0.42

2021/05/10 12:39:32 INFO mlflow.utils.conda: === Creating conda environment mlflow-5987e03d4dbaa5faa1a697bb113be9b9bdc39b29 ===
Solving environment: done
Preparing transaction: done
Verifying transaction: done
Executing transaction: done
Installing pip dependencies: / Ran pip subprocess with arguments:
['/home/tomek/miniconda3/envs/mlflow-5987e03d4dbaa5faa1a697bb113be9b9bdc39b29/bin/python', '-m', 'pip', 'install', '-U', '-r', '/home/tomek/AITech/repo/aitech-ium-private/IUM_08/examples/sklearn_elasticnet_wine/condaenv.xf9x7i2v.requirements.txt']
Pip subprocess output:
  Using cached scikit_learn-0.23.2-cp36-cp36m-manylinux1_x86_64.whl (6.8 MB)
  Using cached joblib-1.0.1-py3-none-any.whl (303 kB)
  Using cached scipy-1.5.4-cp36-cp36m-manylinux1_x86_64.whl (25.9 MB)
  Using cached threadpoolctl-2.1.0-py3-none-any.whl (12 kB)
  Using cached pandas-1.1.5-cp36-cp36m-manylinux1_x86_64.whl (9.5 MB)
  Using cached PyYAML-5.4.1-cp36-cp36m-manylinux1_x86_64.whl (640 kB)
  Using cached gunicorn-

2021/05/10 12:42:29 ERROR mlflow.cli: === Run (ID 'b9b3795a2898495d95c650bafc0dcc76') failed ===


# Zadania [10p pkt] (do 16 V 12:00)
1. Dodaj do swojego projektu logowanie parametrów i metryk za pomocą MLflow (polecenia `mlflow.log_param` i `mlflow.log_metric`
2. Dodaj plik MLProject definiujący polecenia do trenowania i testowania, ich parametry wywołania oraz środowisko (użyj zdefiniowanego wcześniej obrazu Docker)